In [0]:
from pyspark.sql.functions import *
from pyspark.sql import Row
from pyspark.sql.types import *

In [0]:
#Lista o diretório dos arquivos e salva em uma variável
arquivo = dbutils.fs.ls('FileStore/tables/csv_sp/')
print(arquivo)

[FileInfo(path='dbfs:/FileStore/tables/csv_sp/dados_A701_D_2024_01_01_2024_07_31.csv', name='dados_A701_D_2024_01_01_2024_07_31.csv', size=12401, modificationTime=1725316480000), FileInfo(path='dbfs:/FileStore/tables/csv_sp/dados_A705_D_2024_01_01_2024_07_31.csv', name='dados_A705_D_2024_01_01_2024_07_31.csv', size=12373, modificationTime=1725316480000), FileInfo(path='dbfs:/FileStore/tables/csv_sp/dados_A706_D_2024_01_01_2024_07_31.csv', name='dados_A706_D_2024_01_01_2024_07_31.csv', size=12267, modificationTime=1725316481000), FileInfo(path='dbfs:/FileStore/tables/csv_sp/dados_A707_D_2024_01_01_2024_07_31.csv', name='dados_A707_D_2024_01_01_2024_07_31.csv', size=12878, modificationTime=1725316481000), FileInfo(path='dbfs:/FileStore/tables/csv_sp/dados_A708_D_2024_01_01_2024_07_31.csv', name='dados_A708_D_2024_01_01_2024_07_31.csv', size=12658, modificationTime=1725316481000), FileInfo(path='dbfs:/FileStore/tables/csv_sp/dados_A711_D_2024_01_01_2024_07_31.csv', name='dados_A711_D_2024

In [0]:
#Looping para percorrer a lista
for i in arquivo:
     
    csv = f"/FileStore/tables/csv_sp/{i.name}"
    
    #Condição para ter certeza que apenas arquivos .csv serão lidos
    if csv.endswith(".csv"):
        
        #Abre o arquivo csv
        df_csv = spark.read\
        .format("csv")\
        .option("sep", ";")\
        .option("skipRows", 10)\
        .option("header", True)\
        .option("inferSchema", True)\
        .load(csv)

        #Realiza nova leitura do arquivo
        df = spark.read\
        .format("csv")\
        .option("sep", ";")\
        .load(csv)

        #Filtra pelas primeiras 5 linhas
        df = df.limit(5)
        local = df.collect()

        #Realiza a extração do nome da cidade, localização, altura e código da estação
        j = []
        for locais in local:
                nome_completo = locais._c0.split(':')[1]
                j.append(nome_completo)
       

        #Convertendo todas as colunas para double
        colunas = df_csv.columns
        
        for coluna in colunas:

                if coluna != 'Data Medicao':
                        df_csv = df_csv.withColumn(coluna, regexp_replace(df_csv[coluna], ',', '.').cast("double"))

        #Passa os valores das primeiras linhas do arquivo
        df_csv = df_csv.withColumn("Cidade", lit(j[0]))
        df_csv = df_csv.withColumn("Codigo_Estacao", lit(j[1]))
        df_csv = df_csv.withColumn("Latitude", lit(j[2]))
        df_csv = df_csv.withColumn("Longitude", lit(j[3]))
        df_csv = df_csv.withColumn("Altitude", lit(j[4]))

        df_csv = df_csv.na.drop() #Realiza a remoção de linhas com dados nulos
        df_csv = df_csv.dropDuplicates() #Remove linhas duplicadas
        
        #Cria view temporária
        df_csv.createOrReplaceTempView('tb_csv')

        #Cria tabela
        spark.sql("""CREATE TABLE IF NOT EXISTS raw_csv (
        Data_Medicao date,
        PRECIPITACAO_TOTAL_DIARIO_AUT_mm double,
        PRESSAO_ATMOSFERICA_MEDIA_DIARIA_AUT_mB double,
        TEMPERATURA_DO_PONTO_DE_ORVALHO_MEDIA_DIARIA_AUT_C double,
        TEMPERATURA_MAXIMA_DIARIA_AUT_C double,
        TEMPERATURA_MEDIA_DIARIA_AUT_C double,
        TEMPERATURA_MINIMA_DIARIA_AUT_C double,
        UMIDADE_RELATIVA_DO_AR_MEDIA_DIARIA_AUT_percen double,
        UMIDADE_RELATIVA_DO_AR_MINIMA_DIARIA_AUT_percen double,
        VENTO_RAJADA_MAXIMA_DIARIA__AUT_ms double,
        VENTO_VELOCIDADE_MEDIA_DIARIA_AUT_ms double,
        Cidade string,
        Codigo_Estacao string,
        Latitude string,
        Longitude string,
        Altitude string
        )
        """)
        
        #Insere os dados na tabela criada
        spark.sql("""INSERT INTO raw_csv
                SELECT * FROM tb_csv
                """)

In [0]:
query = spark.sql("""SELECT * FROM raw_csv""")

query.write\
    .format("csv")\
    .option("header", True)\
    .option("sep", ";")\
    .mode("overwrite")\
    .save("/FileStore/tables/csv_final/estacoes_sp_null.csv")

#Limpa a tabela
display(query)

Data_Medicao PRECIPITACAO_TOTAL_DIARIO_AUT_mm PRESSAO_ATMOSFERICA_MEDIA_DIARIA_AUT_mB TEMPERATURA_DO_PONTO_DE_ORVALHO_MEDIA_DIARIA_AUT_C TEMPERATURA_MAXIMA_DIARIA_AUT_C TEMPERATURA_MEDIA_DIARIA_AUT_C TEMPERATURA_MINIMA_DIARIA_AUT_C UMIDADE_RELATIVA_DO_AR_MEDIA_DIARIA_AUT_percen UMIDADE_RELATIVA_DO_AR_MINIMA_DIARIA_AUT_percen VENTO_RAJADA_MAXIMA_DIARIA__AUT_ms VENTO_VELOCIDADE_MEDIA_DIARIA_AUT_ms Cidade Codigo_Estacao Latitude Longitude Altitude 2024-01-01 20.0 941.0 18.2 27.0 20.3 17.0 88.7 63.0 7.0 0.9 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-02 0.0 939.1 17.6 27.5 20.2 14.8 86.3 61.0 5.6 0.9 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-03 0.0 938.0 18.8 27.3 20.7 15.8 89.8 66.0 10.0 1.1 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-04 3.6 939.3 18.7 23.7 19.8 17.2 93.2 75.0 6.4 1.0 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-05 1.4 939.2 18.9 27.0 20.8 17.3 89.9 64.0 7.3 0.9 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-06 2.6 939.6 19.6 27.2 20.9 18.9 92.8 65.0 6.0 0.6 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-07 2.6 938.6 19.6 31.9 23.4 17.1 82.0 41.0 5.6 0.7 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-08 0.0 937.1 20.1 36.1 26.1 20.1 74.3 29.0 7.9 1.1 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-09 8.2 939.0 20.9 33.3 24.7 19.3 81.8 46.0 8.4 1.1 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-10 7.6 939.0 20.8 32.9 24.7 18.7 81.8 42.0 9.2 1.0 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-11 1.2 937.0 21.5 32.1 25.3 21.5 81.8 51.0 9.1 1.3 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-12 63.6 938.2 20.6 24.4 21.2 20.5 96.5 81.0 9.5 1.2 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-13 2.0 941.9 18.3 22.1 19.2 17.9 94.1 77.0 5.7 1.1 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-14 1.8 941.0 19.5 31.8 22.2 18.0 86.6 47.0 6.8 0.8 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-15 0.0 939.1 21.2 32.3 24.6 17.8 84.0 51.0 8.4 0.9 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-16 0.2 938.6 22.3 33.8 26.3 20.6 81.5 46.0 9.1 1.1 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-17 3.6 939.8 22.9 30.7 23.9 22.4 94.5 60.0 6.1 0.6 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-18 25.0 939.5 21.3 30.3 22.8 18.8 92.6 62.0 6.7 0.5 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-19 18.0 936.9 22.0 32.4 23.6 20.9 91.9 60.0 12.2 1.5 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-20 22.2 934.9 22.4 31.4 24.5 20.7 89.2 59.0 10.6 1.1 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-21 23.0 938.7 20.1 23.8 20.8 18.7 95.9 84.0 8.6 0.8 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-22 16.0 942.2 18.5 24.0 19.7 17.9 93.5 73.0 6.1 0.9 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-23 7.2 941.3 17.2 21.9 18.2 17.0 94.0 73.0 9.0 0.9 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-24 14.2 939.6 16.7 21.9 17.3 14.9 96.2 85.0 9.0 1.0 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-25 11.2 940.2 16.1 18.9 16.5 15.3 97.3 89.0 7.9 1.2 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-26 17.4 941.0 16.1 21.1 17.1 15.2 94.2 76.0 6.9 1.0 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-27 5.6 940.3 17.2 24.3 18.7 14.5 91.3 69.0 6.6 0.8 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-28 1.0 940.2 18.1 25.9 19.8 16.3 90.9 63.0 4.2 0.4 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-29 2.4 939.3 18.8 29.3 20.7 16.4 90.3 54.0 8.6 0.9 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-30 37.2 938.4 18.8 30.0 21.1 15.1 88.4 49.0 5.9 0.5 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-01-31 1.6 939.8 20.5 28.8 22.1 18.8 91.5 61.0 5.3 0.5 BARRA DO TURVO A746 -24.96277777 -48.41638888 659.89 2024-02-01 7.2 942.6 19.6 25.3 20.9 17.5 92.7 75.0 5.9 0.5 BARRA 

In [0]:
spark.sql("""TRUNCATE TABLE raw_csv""")

DataFrame[]